In [6]:
import pandas as pd

# Read the CSV file
data = pd.read_csv('data/all_combined_data.csv')

# Display the first few rows of the data
data.head()

Input             Tags
0  Title: What is the effective differencial effe...  ['electronics']
1  Title: Heat sensor with fan cooling Body: Can ...  ['electronics']
2  Title: Outlet Installation--more wires than my...  ['electronics']
3  Title: Buck Converter Operation Question Body:...  ['electronics']
4  Title: Urgent help in area of ASIC design, ver...  ['electronics']

In [7]:
data.tail()

Input  \
162648   Title: Is there an optimal strategy for placi...   
162649   Title: Handling Events Across Multi-Server Ap...   
162650   Title: Is it good practice to use try catch f...   
162651   Title: What do you call a process which trans...   
162652   Title: Testing : Why is it necessary?Body: He...   

                                                    Tags  
162648                      ['algorithms', 'efficiency']  
162649                      ['c#', 'application-design']  
162650                         ['design', 'engineering']  
162651  ['python', 'naming', 'parsing', 'serialization']  
162652                                       ['testing']

In [ ]:
data['Tags'] = data['Tags'].apply(lambda tags: tags + ['ignore'] if len(tags) == 1 else tags)

In [5]:
data.head()

Input             Tags
0  Title: What is the effective differencial effe...  ['electronics']
1  Title: Heat sensor with fan cooling Body: Can ...  ['electronics']
2  Title: Outlet Installation--more wires than my...  ['electronics']
3  Title: Buck Converter Operation Question Body:...  ['electronics']
4  Title: Urgent help in area of ASIC design, ver...  ['electronics']

In [13]:
data.head()

Input                   Tags
0  Title: What is the effective differencial effe...  [electronics, ignore]
1  Title: Heat sensor with fan cooling Body: Can ...  [electronics, ignore]
2  Title: Outlet Installation--more wires than my...  [electronics, ignore]
3  Title: Buck Converter Operation Question Body:...  [electronics, ignore]
4  Title: Urgent help in area of ASIC design, ver...  [electronics, ignore]

In [ ]:
from sklearn.preprocessing import MultiLabelBinarizer
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.ensemble import RandomForestClassifier
from sklearn.multioutput import MultiOutputClassifier
from sklearn.model_selection import train_test_split
from sklearn.metrics import classification_report


df = data[['Input', 'Tags']].copy()
import ast

df["Tags"] = df["Tags"].apply(ast.literal_eval)

# Step 1: One-hot encode the tags
mlb = MultiLabelBinarizer()
y = mlb.fit_transform(df["Tags"])

# Step 2: TF-IDF on Input column
tfidf = TfidfVectorizer(max_features=5000)
X = tfidf.fit_transform(df["Input"])

# Step 3: Train-test split
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# Step 4: Train Random Forest in MultiOutputClassifier
rf = RandomForestClassifier(n_estimators=100, random_state=42)
multi_rf = MultiOutputClassifier(rf)
multi_rf.fit(X_train, y_train)

# Step 5: Predict and evaluate
y_pred = multi_rf.predict(X_test)
print(classification_report(y_test, y_pred, target_names=mlb.classes_))
# Step 6: Save the model
import joblib
joblib.dump(multi_rf, 'multi_rf_model.pkl')
# Step 7: Save the TF-IDF vectorizer
joblib.dump(tfidf, 'tfidf_vectorizer.pkl')
# Step 8: Save the label binarizer
joblib.dump(mlb, 'mlb.pkl')
# Step 9: Load the model and vectorizer
loaded_model = joblib.load('multi_rf_model.pkl')
loaded_vectorizer = joblib.load('tfidf_vectorizer.pkl')
loaded_mlb = joblib.load('mlb.pkl')



NameError: name 'data' is not defined

In [27]:
import numpy as np

print("Decoded tags:", mlb.inverse_transform(np.array([y[0]]))[0])


Decoded tags: ('electronics',)


In [21]:
import ast

df["Tags"] = df["Tags"].apply(ast.literal_eval)


In [22]:
print(df["Tags"].head())
print(type(df["Tags"].iloc[0]))


0    [electronics]
1    [electronics]
2    [electronics]
3    [electronics]
4    [electronics]
Name: Tags, dtype: object
<class 'list'>


In [23]:
y = mlb.fit_transform(df["Tags"])


In [24]:
print("Decoded tags:", mlb.inverse_transform(np.array([y[0]]))[0])


Decoded tags: ('electronics',)


In [26]:
y[0]

array([0, 0, 0, ..., 0, 0, 0], shape=(13158,))

In [25]:
data.dtypes

Input    object
Tags     object
dtype: object

In [9]:
from sklearn.metrics import accuracy_score

# Calculate accuracy for each label and then average
accuracies = [accuracy_score(y_test[:, i], y_pred[:, i]) for i in range(y_test.shape[1])]
average_accuracy = sum(accuracies) / len(accuracies)

print(f"Average Accuracy: {average_accuracy}")

Average Accuracy: 0.9140289373926052


In [14]:
single_tag_rows = df[df['Tags'].apply(len) <= 3]
print(single_tag_rows)

Empty DataFrame
Columns: [Input, Tags]
Index: []


In [1]:
from sklearn.ensemble import RandomForestClassifier
from sklearn.multioutput import MultiOutputClassifier
from sklearn.model_selection import train_test_split
from sklearn.metrics import classification_report
import numpy as np

# Example: X has 100 samples, 20 features; y has 100 samples, 3 possible labels per sample
X = np.random.rand(100, 20)
y = np.random.randint(2, size=(100, 3))  # Binary presence/absence for 3 labels

# Train-test split
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# Initialize base RandomForest classifier
rf = RandomForestClassifier(n_estimators=100, random_state=42)

# Wrap it for multi-label classification
multi_rf = MultiOutputClassifier(rf)

# Train the model
multi_rf.fit(X_train, y_train)

# Predict
y_pred = multi_rf.predict(X_test)

# Evaluate
print(classification_report(y_test, y_pred))


              precision    recall  f1-score   support

           0       0.35      0.67      0.46         9
           1       1.00      0.09      0.17        11
           2       0.91      0.71      0.80        14

   micro avg       0.59      0.50      0.54        34
   macro avg       0.75      0.49      0.48        34
weighted avg       0.79      0.50      0.51        34
 samples avg       0.51      0.48      0.45        34



/home/darth/.pyenv/versions/3.10.12/envs/major02/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in samples with no predicted labels. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/home/darth/.pyenv/versions/3.10.12/envs/major02/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 in samples with no true labels. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))


In [4]:
y_train[3]

array([0, 1, 1])